In [44]:
from BAC0.tools import const

FILE_HEADER = const.FILE_HEADER
FILE_FOOTER = const.FILE_FOOTER
TAG = const.TAG

template_example = {
    "names" : [("name", "dev_id")],
}

def convert(d, device_name=None, make_template=False):
    """
    Template : If true, will not populate name and device id so the file
    can be reused to create a dictionnary in T3 Studio with multiple
    devices. This will prevents us from switching dictionnary all the time.
    """
    list_of_tags = []
    device_id = None
    OBJECT_TYPE = {
        "analogValue": "AV",
        "analogInput": "AI",
        "analogOutput": "AO",
        "binaryInput": "BI",
        "binaryValue": "BV",
        "binaryOutput": "BO",
        "multiStateInput": "MI",
        "multiStateValue": "MV",
        "multiStateOutput": "MO",
    }
    DATATYPES = {
        "AI": "float",
        "AO": "float",
        "AV": "float",
        "BI": "boolean",
        "BO": "boolean",
        "BV": "boolean",
        "MI": "unsignedInt",
        "MO": "unsignedInt",
        "MV": "unsignedInt",
    }

    WRITE_PRIORITY = {
        "AI": 0,
        "AO": 8,
        "AV": 10,
        "BI": 0,
        "BO": 8,
        "BV": 10,
        "MI": 0,
        "MO": 8,
        "MV": 10,
    }

    if make_template:
        device_name = "$DEVICE_NAME"
        device_id = "$DEVICE_ID"

    data = {}
    for each in d.points:
        name = device_name if device_name else d.properties.name
        data["name"] = "{}/{}".format(name, each.properties.name)
        data["group"] = ""
        data["object_type"] = OBJECT_TYPE[each.properties.type]
        data["object_instance"] = each.properties.address
        data["device_id"] = device_id if device_id else d.properties.device_id
        data["data_type"] = DATATYPES[data["object_type"]]
        data["object_property"] = 85
        data["write_priority"] = WRITE_PRIORITY[data["object_type"]]
        data["cov"] = "false"
        data["refresh_time"] = 1000
        data["access_mode"] = "READ"
        data["active"] = "false"
        data["comment"] = each.properties.description
        data["array_index"] = -1
        list_of_tags.append(TAG.format(d=data))

    return (name, list_of_tags)

def build_from_templates(list_of_tags, config=None):
    """
    Config must be a list of tuple (name, device_id)
    """
    _lst_of_tags = []
    for each in config:
        name, device_id = each
        for each in list_of_tags:
            print(each)
            each = each.replace("$DEVICE_NAME", name)
            each = each.replace("DEVICE_ID", "{}".format(device_id))
            print(each)
            _lst_of_tags.append(each)
    return _lst_of_tags


def merge_templates(lst=[]):
    _lst = []
    for each in lst:
        _lst.extend(each)
    return _lst



def write_tags_import_file(name, list_of_tags):
    _content = FILE_HEADER
    for tag in list_of_tags:
        _content += tag
    _content += FILE_FOOTER
    with open("{}.xml".format(name), "w") as xml_file:
        xml_file.write(_content)



In [28]:
import BAC0
bacnet = BAC0.lite()
uc = BAC0.device('303:5', 5905, bacnet)
nep = BAC0.device('303:20', 153020, bacnet)

2022-02-02 22:08:28,735 - INFO    | Starting BAC0 version 22.01.06dev (Lite)
2022-02-02 22:08:28,736 - INFO    | Use BAC0.log_level to adjust verbosity of the app.
2022-02-02 22:08:28,737 - INFO    | Ex. BAC0.log_level('silence') or BAC0.log_level('error')
2022-02-02 22:08:29,040 - INFO    | Using ip : 192.168.211.54


InitializationError: IP Address provided (192.168.211.54) already used by BAC0. Check if another software is using port 47808 on this network interface. If so, you can define multiple IP per interface. Or specify another IP using BAC0.lite(ip='IP/mask')

In [29]:
uc_template = convert(uc, make_template=True)
nep_template = convert(nep, make_template=True)

In [26]:
uc_template[1][2]

'    <tag>\n        <name>$DEVICE_NAME/DAP-SP</name>\n        <group></group>\n        <resourceLocator>\n            <protocolName>BACN</protocolName>\n            <object_type>AV</object_type>\n            <device_id>$DEVICE_ID</device_id>\n            <data_type>float</data_type>\n            <arraysize></arraysize>\n            <conversion></conversion>\n            <object_instance>19</object_instance>\n            <object_property>85</object_property>\n            <array_index>-1</array_index>\n            <write_priority>10</write_priority>\n            <cov>false</cov>\n        </resourceLocator>\n        <encoding></encoding>\n        <refreshTime>1000</refreshTime>\n        <accessMode>READ</accessMode>\n        <active>false</active>\n        <TAGLOCATOR></TAGLOCATOR>\n        <comment></comment>\n        <simulator>\n            <DataSimulator>Variables</DataSimulator>\n            <Amplitude></Amplitude>\n            <Simulator_offset></Simulator_offset>\n            <Peri

In [49]:
_nep = [("TP101", 331908),
        ("TP102", 331909),
        ("TP102_1", 331910),
        ("TP104", 331911),
        ("TP105", 331912),
        ("TP106", 331913),
        ("TP111", 331914),
        ("TP112", 331915),
        ("TP113A", 331916),
        ("TP113B", 331917),
        ]
_neptags = build_from_templates(nep_template[1], _nep)
_uc = [("PCG-9-004", 5904),
        ("PCG-9-005", 5905),
        ("PCG-9-006", 5906)
        ]
_uctags = build_from_templates(uc_template[1], _uc)
write_tags_import_file("CCB",merge_templates([_uctags,_neptags]))

    <tag>
        <name>$DEVICE_NAME/Intern_Temp</name>
        <group></group>
        <resourceLocator>
            <protocolName>BACN</protocolName>
            <object_type>AI</object_type>
            <device_id>$DEVICE_ID</device_id>
            <data_type>float</data_type>
            <arraysize></arraysize>
            <conversion></conversion>
            <object_instance>1</object_instance>
            <object_property>85</object_property>
            <array_index>-1</array_index>
            <write_priority>0</write_priority>
            <cov>false</cov>
        </resourceLocator>
        <encoding></encoding>
        <refreshTime>1000</refreshTime>
        <accessMode>READ</accessMode>
        <active>false</active>
        <TAGLOCATOR></TAGLOCATOR>
        <comment>Intern_Temp</comment>
        <simulator>
            <DataSimulator>Variables</DataSimulator>
            <Amplitude></Amplitude>
            <Simulator_offset></Simulator_offset>
            <Period></Period>


In [47]:
write_tags_import_file("NEPTRONICS", _tags)